In [17]:
# General imports
import os
import time
import random
import datetime
import glob
import pickle
import tqdm
import copy
import optuna
import numpy as np
import pandas as pd
import scipy as sp
import matplotlib.pyplot as plt
import seaborn as sns
import mne
from rich import print as rprint
from rich.pretty import pprint as rpprint
from tqdm import tqdm
from itertools import chain
from functools import partial

# JAX + Keras
os.environ["KERAS_BACKEND"] = "jax"
os.environ["TF_USE_LEGACY_KERAS"] = "0"
import jax
import jax.numpy as jnp
import keras
from keras.models import Model
from keras.layers import Dense, Activation, Permute, Dropout
from keras.layers import Conv2D, MaxPooling2D, AveragePooling2D, Conv1D, MaxPooling1D, AveragePooling1D
from keras.layers import SeparableConv2D, DepthwiseConv2D
from keras.layers import BatchNormalization
from keras.layers import SpatialDropout2D
from keras.regularizers import l1_l2
from keras.layers import Input, Flatten
from keras.constraints import max_norm
from keras import backend as K

# Sklearn
from sklearn.preprocessing import LabelEncoder, StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix

from keras.models import Sequential
from keras.layers import LSTM, Dense, Dropout, TimeDistributed, BatchNormalization
import h5py
from sklearn import preprocessing

# Dataset
from custom_datasets.fatigue_mi import FatigueMI

%load_ext autoreload
%autoreload 3

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [18]:
SKLRNG = 42
RNG = jax.random.PRNGKey(SKLRNG)

#### Dataset

In [21]:
def data_generator(dataset, subjects = [1], channel_idx = [], filters = ([8, 32],), sfreq = 250):
    
    find_events = lambda raw, event_id: mne.find_events(raw, shortest_event=0, verbose=False) if len(mne.utils._get_stim_channel(None, raw.info, raise_error=False)) > 0 else mne.events_from_annotations(raw, event_id=event_id, verbose=False)[0]
    
    data = dataset.get_data(subjects=(subjects if len(subjects) > 0 else dataset.subject_list))
    
    X = []
    y = []
    metadata = []

    for subject_id in data.keys():
        for session_id in data[subject_id].keys():
            for run_id in data[subject_id][session_id].keys():
                raw = data[subject_id][session_id][run_id]
                
                for fmin, fmax in filters:
                    raw = raw.filter(l_freq = fmin, h_freq = fmax, method = 'iir', picks = 'eeg', verbose = False)
                
                events = find_events(raw, dataset.event_id)

                tmin = dataset.interval[0]
                tmax = dataset.interval[1]

                channels = np.asarray(raw.info['ch_names'])[channel_idx] if len(channel_idx) > 0 else np.asarray(raw.info['ch_names'])

                # rpprint(channels)
                
                stim_channels = mne.utils._get_stim_channel(None, raw.info, raise_error=False)
                picks = mne.pick_channels(raw.info["ch_names"], include=channels, exclude=stim_channels, ordered=True)

                x = mne.Epochs(
                    raw,
                    events,
                    event_id=dataset.event_id,
                    tmin=tmin,
                    tmax=tmax,
                    proj=False,
                    baseline=None,
                    preload=True,
                    verbose=False,
                    picks=picks,
                    event_repeated="drop",
                    on_missing="ignore",
                )
                x_events = x.events
                inv_events = {k: v for v, k in dataset.event_id.items()}
                labels = [inv_events[e] for e in x_events[:, -1]]

                # rpprint({
                #     "X": np.asarray(x.get_data(copy=False)).shape,
                #     "y": np.asarray(labels).shape,
                #     "channels selected": np.asarray(raw.info['ch_names'])[channel_idx]
                # })

                # x.plot(scalings="auto")
                
                x_resampled = x.resample(sfreq) if sfreq != raw.info['sfreq'] else x # Resampler_Epoch
                x_resampled_data = x_resampled.get_data(copy=False) # Convert_Epoch_Array
                x_resampled_data_standard_scaler = np.asarray([
                    StandardScaler().fit_transform(x_resampled_data[i])
                    for i in np.arange(x_resampled_data.shape[0])
                ]) # Standard_Scaler_Epoch

                n = x_resampled_data_standard_scaler.shape[0] if sfreq != 250 else x.get_data(copy=False).shape[0]
                # n = x.get_data(copy=False).shape[0]
                met = pd.DataFrame(index=range(n))
                met["subject"] = subject_id
                met["session"] = session_id
                met["run"] = run_id
                x.metadata = met.copy()
                
                # X.append(x_resampled_data_standard_scaler)
                X.append(x)
                y.append(labels)
                metadata.append(met)

    return np.concatenate(X, axis=0), np.concatenate(y), pd.concat(metadata, ignore_index=True)

fat_dataset = FatigueMI()
X, y, _ = data_generator(fat_dataset, subjects=[1], channel_idx=[], sfreq=128) # if channel_idx=[], all channels will be used

Adding metadata with 3 columns


#### Models

In [22]:
def lstm_cnn_net(nb_classes, channels, samples, dropout_rate_1 = 0.5, dropout_rate_2 = 0.5):
    model = Sequential()
    model.add(Input(shape=(samples, channels)))

    # add 1-layer cnn
    model.add(Conv1D(40, kernel_size=20, strides=4))
    model.add(Activation('relu'))
    model.add(Dropout(dropout_rate_1))
    model.add(BatchNormalization())
    model.add(MaxPooling1D(pool_size=4, strides=4))


    # add 1-layer lstm
    model.add(LSTM(50, return_sequences=True, stateful=False))
    # model.add(LSTM(128, return_sequences=True, stateful=False))
    # model.add(LSTM(32, return_sequences=True, stateful=False))
    model.add(Dropout(dropout_rate_2))
    model.add(BatchNormalization())
    model.add(Flatten())
    model.add(Dense(nb_classes, activation='softmax'))
    
    return model


#### Heuristic search for hyperparameter optimization

In [28]:
def objective_fn(trial, subjects=[], model_str = "lstm_cnn_net", **kwargs):
    _SFREQ_ = 128
    _TRAIN_SIZE_ = 0.8
    _TEST_SIZE_ = 1 - _TRAIN_SIZE_
    _BATCH_SIZE = 256

    models = {
        "lstm_cnn_net": lstm_cnn_net
    }

    subjects = subjects if len(subjects) > 0 else fat_dataset.subject_list
    model_fn = models[model_str]
    
    channels_dict = { k: trial.suggest_categorical(f"channels_{k}", [True, False]) for k in fat_dataset.get_data(subjects=[1])[1]['0']['0'].info['ch_names'][:-1] }
    channels_idx = [i for i, v in enumerate(channels_dict.values()) if v]
    while len(channels_idx) == 0:
        channels_dict = { k: trial.suggest_categorical(f"channels_{k}", [True, False]) for k in fat_dataset.get_data(subjects=[1])[1]['0']['0'].info['ch_names'][:-1] }
        channels_idx = [i for i, v in enumerate(channels_dict.values()) if v]
    
    X, y, _ = data_generator(fat_dataset, subjects=subjects, channel_idx=channels_idx, sfreq=_SFREQ_)
    
    _NUM_SAMPLES_ = X.shape[-1]
    _NUM_CHANNELS_ = X.shape[-2]
    
    y_encoded = LabelEncoder().fit_transform(y)
    _NUM_CLASSES_ = len(np.unique(y_encoded))
    X_train, X_test, y_train, y_test = train_test_split(X.reshape(-1, _NUM_SAMPLES_, _NUM_CHANNELS_), y_encoded, test_size=_TEST_SIZE_, random_state=SKLRNG, stratify=None, shuffle=False)
    # X_train, X_test, y_train, y_test = train_test_split(X.reshape(-1, _NUM_SAMPLES_, _NUM_CHANNELS_), y_encoded, test_size=_TEST_SIZE_, random_state=SKLRNG, stratify=y_encoded)
    
    model_params = {
        "nb_classes": _NUM_CLASSES_,
        "channels": _NUM_CHANNELS_,
        "samples": _NUM_SAMPLES_,
    }
    
    model = model_fn(**model_params)
    model.compile(
        loss="sparse_categorical_crossentropy", 
        optimizer="adam", 
        metrics=["accuracy"]
    )
    
    history = model.fit(
        X_train,
        y_train,
        batch_size=_BATCH_SIZE,
        epochs=100,
        validation_split=0.2,
        shuffle=True,
        callbacks=[
            # keras.callbacks.EarlyStopping(monitor="val_loss", patience=75, restore_best_weights=True),
            # keras.callbacks.ReduceLROnPlateau(monitor="val_loss", patience=75, factor=0.5)
            keras.callbacks.EarlyStopping(monitor="val_loss", patience=10, restore_best_weights=True),
            keras.callbacks.ReduceLROnPlateau(monitor="val_loss", patience=3, factor=0.1)
        ],
    )

    trial.set_user_attr("trial_data", {
        "channels_selected": np.asarray(fat_dataset.get_data(subjects=[1])[1]['0']['0'].info['ch_names'])[channels_idx],
        # "history": history,
        "model": model.to_json(),
        "val_accuracy": history.history["val_accuracy"],
        "test_accuracy": model.evaluate(X_test, y_test, batch_size=_BATCH_SIZE)[1]
    })

    # return (1 - np.mean(history.history["val_accuracy"][-2:])) + 0.005*len(channels_idx)
    return (1 - history.history["val_accuracy"][-1])**2 + 5e-5*len(channels_idx)

def heuristic_optimizer(obj_fn, max_iter = 15, show_progress_bar = True, subjects=[], model_str="lstm_cnn_net", **kwargs):
    
    optuna.logging.set_verbosity(optuna.logging.CRITICAL)

    objective = partial(obj_fn, subjects = subjects, model_str = model_str)
    
    study = optuna.create_study(direction="minimize", sampler=optuna.samplers.NSGAIISampler())
    study.optimize(objective, n_trials=max_iter, show_progress_bar=show_progress_bar, callbacks=[], **kwargs)
    
    return study

#### Search for best subjects

In [29]:
subject_results = {}

for subject in fat_dataset.subject_list:
   study = heuristic_optimizer(objective_fn, subjects=[subject], model_str="lstm_cnn_net")
   subject_results[subject] = study.best_trial
   rpprint({
      "subject": subject,
      "test_accuracy": study.best_trial.user_attrs["trial_data"]["test_accuracy"],
      "val_accuracy": study.best_trial.user_attrs["trial_data"]["val_accuracy"][-1],
      "channels_selected": study.best_trial.user_attrs["trial_data"]["channels_selected"]
   })

  0%|          | 0/15 [00:00<?, ?it/s]

Adding metadata with 3 columns
Epoch 1/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 2s 2s/step - accuracy: 0.5588 - loss: 1.0788 - val_accuracy: 0.6111 - val_loss: 0.6035 - learning_rate: 0.0010
Epoch 2/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step - accuracy: 0.5441 - loss: 0.9715 - val_accuracy: 0.5556 - val_loss: 0.5984 - learning_rate: 0.0010
Epoch 3/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step - accuracy: 0.5147 - loss: 1.0371 - val_accuracy: 0.6111 - val_loss: 0.6048 - learning_rate: 0.0010
Epoch 4/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step - accuracy: 0.5588 - loss: 1.1292 - val_accuracy: 0.6111 - val_loss: 0.6102 - learning_rate: 0.0010
Epoch 5/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step - accuracy: 0.5147 - loss: 0.9492 - val_accuracy: 0.6111 - val_loss: 0.6114 - learning_rate: 0.0010
Epoch 6/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step - accuracy: 0.6176 - loss: 0.7953 - val_accuracy: 0.6111 - val_loss: 0.6140 - learning_rate: 1.0000e-04
Epoch 7/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step - accuracy: 0.558

{
│   'subject': 1,
│   'test_accuracy': 0.5454545617103577,
│   'val_accuracy': 0.6666666865348816,
│   'channels_selected': array(['Fz', 'C4', 'Cz', 'Fp2', 'T3', 'F7', 'T6'], dtype='<U3')
}

  0%|          | 0/15 [00:00<?, ?it/s]

Adding metadata with 3 columns
Epoch 1/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 2s 2s/step - accuracy: 0.5147 - loss: 1.0946 - val_accuracy: 0.5000 - val_loss: 0.6830 - learning_rate: 0.0010
Epoch 2/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step - accuracy: 0.5294 - loss: 0.9939 - val_accuracy: 0.5000 - val_loss: 0.6881 - learning_rate: 0.0010
Epoch 3/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step - accuracy: 0.5294 - loss: 1.0225 - val_accuracy: 0.5556 - val_loss: 0.6854 - learning_rate: 0.0010
Epoch 4/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step - accuracy: 0.5735 - loss: 0.9691 - val_accuracy: 0.5000 - val_loss: 0.6873 - learning_rate: 0.0010
Epoch 5/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 26ms/step - accuracy: 0.4853 - loss: 1.0327 - val_accuracy: 0.5000 - val_loss: 0.6865 - learning_rate: 1.0000e-04
Epoch 6/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step - accuracy: 0.6765 - loss: 0.6937 - val_accuracy: 0.5000 - val_loss: 0.6860 - learning_rate: 1.0000e-04
Epoch 7/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step - accuracy: 0

...

Adding metadata with 3 columns
Epoch 1/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 2s 2s/step - accuracy: 0.5294 - loss: 1.0812 - val_accuracy: 0.5556 - val_loss: 0.7770 - learning_rate: 0.0010
Epoch 2/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 26ms/step - accuracy: 0.4412 - loss: 0.9909 - val_accuracy: 0.5556 - val_loss: 0.7758 - learning_rate: 0.0010
Epoch 3/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step - accuracy: 0.4706 - loss: 0.9483 - val_accuracy: 0.5556 - val_loss: 0.7766 - learning_rate: 0.0010
Epoch 4/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step - accuracy: 0.5735 - loss: 0.8525 - val_accuracy: 0.5556 - val_loss: 0.7637 - learning_rate: 0.0010
Epoch 5/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step - accuracy: 0.5882 - loss: 1.0030 - val_accuracy: 0.5556 - val_loss: 0.7581 - learning_rate: 0.0010
Epoch 6/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step - accuracy: 0.6176 - loss: 0.6779 - val_accuracy: 0.5556 - val_loss: 0.7542 - learning_rate: 0.0010
Epoch 7/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step - accuracy: 0.6765 - 

{
│   'subject': 31,
│   'test_accuracy': 0.5454545617103577,
│   'val_accuracy': 0.7222222089767456,
│   'channels_selected': array(['P3', 'C3', 'Fz', 'Pz', 'Fp2', 'T3', 'O2'], dtype='<U3')
}

  0%|          | 0/15 [00:00<?, ?it/s]

Adding metadata with 3 columns
Epoch 1/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 2s 2s/step - accuracy: 0.4853 - loss: 1.0150 - val_accuracy: 0.5556 - val_loss: 0.7186 - learning_rate: 0.0010
Epoch 2/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 34ms/step - accuracy: 0.4853 - loss: 0.9907 - val_accuracy: 0.5556 - val_loss: 0.7229 - learning_rate: 0.0010
Epoch 3/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step - accuracy: 0.6324 - loss: 0.7661 - val_accuracy: 0.5556 - val_loss: 0.7289 - learning_rate: 0.0010
Epoch 4/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step - accuracy: 0.5588 - loss: 1.0294 - val_accuracy: 0.5556 - val_loss: 0.7302 - learning_rate: 0.0010
Epoch 5/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 26ms/step - accuracy: 0.5882 - loss: 0.9227 - val_accuracy: 0.5556 - val_loss: 0.7318 - learning_rate: 1.0000e-04
Epoch 6/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step - accuracy: 0.6618 - loss: 0.6766 - val_accuracy: 0.5556 - val_loss: 0.7336 - learning_rate: 1.0000e-04
Epoch 7/100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step - accuracy: 0

{
│   'subject': 32,
│   'test_accuracy': 0.5,
│   'val_accuracy': 0.7222222089767456,
│   'channels_selected': array(['P3', 'F3', 'Fz', 'Fp1', 'Fp2', 'T5', 'O2', 'A2', 'T6', 'T4'],
│     dtype='<U3')
}

In [30]:
# Save subject_results
with open(f'subject_results-{datetime.datetime.now().strftime("%Y%m%d-%H%M%S")}.pickle', 'wb') as f:
    pickle.dump(subject_results, f, protocol=pickle.HIGHEST_PROTOCOL)

In [45]:
subject_results_val_acc = { subject: subject_results[subject].user_attrs["trial_data"]["val_accuracy"][-1] for subject in fat_dataset.subject_list }
subject_results_test_acc = { subject: subject_results[subject].user_attrs["trial_data"]["test_accuracy"] for subject in fat_dataset.subject_list }

subject_results_val_acc_df = pd.DataFrame(subject_results_val_acc, index=[0], columns=fat_dataset.subject_list).T.rename(columns={0: 'val_acc'}).sort_values(by='val_acc', ascending=False)
subject_results_test_acc_df = pd.DataFrame(subject_results_test_acc, index=[0], columns=fat_dataset.subject_list).T.rename(columns={0: 'test_acc'}).sort_values(by='test_acc', ascending=False)

subject_results_acc_df = subject_results_val_acc_df.join(subject_results_test_acc_df)

subject_results_acc_df

val_acc  test_acc
17  0.888889  0.500000
29  0.833333  0.590909
12  0.777778  0.409091
5   0.777778  0.545455
6   0.777778  0.454545
28  0.777778  0.590909
24  0.777778  0.454545
31  0.722222  0.545455
25  0.722222  0.500000
23  0.722222  0.500000
22  0.722222  0.545455
32  0.722222  0.500000
3   0.722222  0.590909
4   0.722222  0.636364
9   0.722222  0.500000
8   0.722222  0.545455
1   0.666667  0.545455
27  0.666667  0.500000
30  0.666667  0.500000
18  0.666667  0.500000
7   0.666667  0.636364
20  0.666667  0.590909
21  0.666667  0.590909
11  0.666667  0.500000
14  0.666667  0.636364
26  0.666667  0.500000
13  0.611111  0.454545
19  0.611111  0.590909
2   0.611111  0.772727
16  0.611111  0.545455
15  0.611111  0.454545
10  0.555556  0.500000